# HIP (Heterogeneous-Compute Interface for Portability)

* 1 to 1 CUDA clone, e.g. `cudaMalloc` -> `hipMalloc`
* Not all CUDA features and libraries are available
* LLVM / Regex based CUDA to HIP converter: `hipify-clang` / `hipify-perl`
  <!--  * ZLUDA: allow CUDA binaries to run on AMD GPU
        * SCALE compiler (Spectral Compute): drop-in replacement to NVIDIA's nvcc -->
* Open source (MIT License)
* Links to external resources:
  * [HIP documentation](https://rocm.docs.amd.com/projects/HIP/en/latest/)

## Supported Compilers

* AMD ROCm Compiler
* LLVM

## Hardware portability

* AMD GPUs (ROCm backend)
* NVIDIA GPUs (CUDA backend)

## Example Code

* Source code available in [exampleHIP.cpp](../src/exampleHIP.cpp)

* Include HIP Support into your code

  ```c++
  #include "hip/hip_runtime.h"

  int main() {
      // ...

      return 0;
  }
  ```

* Platform information

  ```c++
  int runtime_version = 0;
  error_id = hipRuntimeGetVersion(&runtime_version);
  cout << "HIP version: "
       << runtime_version / 1000 << "." << (runtime_version % 100) / 10
       << endl;

  int driver_version = 0;
  error_id = hipDriverGetVersion(&driver_version);
  cout << "HIP driver version: "
       << driver_version / 1000 << "." << (driver_version % 100) / 10
       << endl;

  int num_devices = 0;
  error_id = hipGetDeviceCount(&num_devices);
  if (error_id == hipErrorNoDevice || num_devices == 0) {
    errx(1, "No HIP device found");
  }
  cout << "Number of HIP devices: " << num_devices << endl;

  int device_num = 0;
  error_id = hipSetDevice(device_num);
  cout << "HIP Device number: " << device_num << endl;

  size_t memory_free = 0, memory_total = 0;
  error_id = hipMemGetInfo(&memory_free, &memory_total);
  cout << "Memory on HIP device: "
       << memory_total / (1024. * 1024. * 1024.) << " GiB"
       << endl;
  cout << "Free Memory on HIP device: "
       << memory_free / (1024. * 1024. * 1024.) << " GiB"
       << endl;

  hipDeviceProp_t device_properties;
  error_id = hipGetDeviceProperties(&device_properties, device_num);
  cout << "HIP device name: "
       << device_properties.name
       << endl;
  cout << "HIP device capability: "
       << device_properties.major << "." << device_properties.minor
       << endl;
  cout << "HIP device max clock rate: "
       << device_properties.clockRate / 1000000. << " GHz"
       << endl;
  cout << "HIP device max memory clock rate: "
       << device_properties.memoryClockRate / 1000000. << " GHz"
       << endl;
  cout << "HIP device compute mode: "
       << device_properties.computeMode
       << endl;

  if (!device_properties.arch.hasDoubles) {
      errx(1, "HIP device does not support doubles");
  }
  ```

* A list of devices can be obtained by `rocminfo`
* Device selection can be done by setting environment variables `ROCR_VISIBLE_DEVICES` or `HIP_VISIBLE_DEVICES`

* Allocate memory on the host

  ```c++
  double *a = (double *) malloc(size * sizeof(double));
  if (a == NULL) {
      errx(1, "malloc a[] failed");
  }
  ```

* Allocate memory on the device

  ```c++
  double *device_a;
  if (hipMalloc(&device_a, size * sizeof(double)) != hipSuccess) {
      errx(1, "hipMalloc device_a[] failed");
  }
  ```

* Pre-process / initialize data on the host
  e.g. read data from storage

  ```c++
  for (unsigned int i = 0; i < size; i++) {
      a[i] = 1.;
  }
  ```

* Copy data from the host to the device

  ```c++
  error_id = hipMemcpy(device_a, a, size * sizeof(double), hipMemcpyHostToDevice);
  ```

* Compute kernel definition

  ```c++
   __global__ void inc_kernel(double *device_a) {
      const int i = blockDim.x * blockIdx.x + threadIdx.x;
      device_a[i]++;
  }
  ```

* Compute on the device

  ```c++
  int blockSize = 256;
  int numBlocks = size / blockSize;
  inc_kernel<<<numBlocks, blockSize>>>(device_a);
  ```

* Transfer data back from the device to the host

  ```c++
  error_id = hipMemcpy(a, device_a, size * sizeof(double), hipMemcpyDeviceToHost);
  ```

* Delete data on the device

  ```c++
  error_id = hipFree(device_a);
  ```

* Post-process data on the host
  e.g. write data to storage

  ```c++
  for (unsigned int i = 0; i < size; i++) {
     if (a[i] != 2.) {
         errx(2, "Computation on GPU failed");
     }
  }
  ```

* Free memory on the host

  ```c++
  free(a);
  ```

### Compilation

In [ ]:
#!/usr/bin/bash
# LLVM
! clang++-21 \
    -O2 -march=native -Wall -Wextra -fuse-ld=lld -Wl,-rpath=/usr/lib/llvm-21/lib \
    -x hip --hip-link --offload-arch=native -foffload-lto \
    "../src/exampleHIP.cpp" -o "../bin/exampleHIP"

In [ ]:
#!/usr/bin/bash
# AMD ROCm Compiler with CUDA Backend
! export HIP_PLATFORM=nvidia; \
  hipcc -ccbin='gcc' --forward-unknown-to-host-compiler -O2 -march=native -Wall -Wno-deprecated-declarations -I/opt/rocm/include/ \
      --gpu-architecture=native \
      "../src/exampleHIP.cpp" -o "../bin/exampleHIP"

In [7]:
#!/usr/bin/bash
# AMD ROCm Compiler
! hipcc -O2 -march=native -flto -Wall -Wextra \
    --offload-arch=native -foffload-lto \
    "../src/exampleHIP.cpp" -o "../bin/exampleHIP"

### Execution

In [8]:
#!/usr/bin/bash
! ../bin/exampleHIP

HIP version: 60443.8
HIP driver version: 60443.8
Number of HIP devices: 1
HIP Device number: 0
Memory on HIP device: 7.98438 GiB
Free Memory on HIP device: 7.92773 GiB
HIP device name: AMD Radeon RX 6600
HIP device capability: 10.3
HIP device max clock rate: 2.75 GHz
HIP device max memory clock rate: 0.875 GHz
HIP device compute mode: 0
* Allocate memory on the host
* Allocate memory on the device
* Pre-process / initialize data on the host
  e.g. read data from storage
* Copy data from the host to the device
* Compute on the device
* Transfer data back from the device to the host
* Delete data on the device
* Post-process data on the host
  e.g. write data to storage
* Free memory on the host
